In [2]:
import numpy as np
import pandas as pd

from sklearn.metrics import confusion_matrix
from sklearn.metrics import roc_auc_score, auc
from sklearn.metrics import precision_recall_curve
from sklearn.metrics import classification_report
from collections import Counter
import re
from tqdm import trange

In [3]:
database_data = pd.read_csv('database_file汇总.csv').drop_duplicates()
database_data

miRNA miRBase Update ID              disease   Cancer Subtype
0       hsa-miR-106a   hsa-miR-106a-5p             lymphoma  B cell lymphoma
1         hsa-let-7g     hsa-let-7g-5p             lymphoma  B cell lymphoma
2      hsa-miR-17-5p     hsa-miR-17-5p             lymphoma  B cell lymphoma
3         hsa-let-7f     hsa-let-7f-5p             lymphoma  B cell lymphoma
4         hsa-let-7a     hsa-let-7a-5p             lymphoma  B cell lymphoma
...              ...               ...                  ...              ...
98742    hsa-mir-34a               NaN        Glioblastoma               NaN
98747    hsa-mir-15b               NaN   Stomach Neoplasms               NaN
98748   hsa-mir-16-1               NaN   Stomach Neoplasms               NaN
98749   hsa-mir-16-2               NaN   Stomach Neoplasms               NaN
98755   hsa-mir-449a               NaN  Prostatic Neoplasms              NaN

[59765 rows x 4 columns]

In [4]:
def new_MDA(results_df, task, balanced = True):
    new_MDA = results_df[results_df['y_true'] == 0][results_df['y_pred'] == 1]
    if balanced:
        new_MDA.to_csv(task + '_balanced_new_MDA.csv')
    else:
        new_MDA.to_csv(task + '_unbalanced_new_MDA.csv')
        
    new_MDA_simplied = new_MDA[['miRNA_y', 'disease_y', 'y_prob']]

    temp = []
    for item in new_MDA_simplied['disease_y'].tolist():
        item = item.replace("['",'').replace("']", "")
        temp.append(item)
    new_MDA_simplied['disease_newMDA'] = temp
    
    return new_MDA, new_MDA_simplied

In [5]:
def database_data_miRNA_in_newMDA_results(database_data, new_MDA_simplied):
    database_data_miRNA_in_results = database_data[database_data['miRNA'].isin(new_MDA_simplied['miRNA_y'])]
    database_data_miRNA_in_results_2 = database_data[database_data['miRBase Update ID'].isin(new_MDA_simplied['miRNA_y'])]
    if database_data_miRNA_in_results_2.shape[0] != 0:
        print('miRBase Update ID shoud be used!!!!!!')
        database_data_miRNA_in_results = pd.concat([database_data_miRNA_in_results, ], axis = 0)
    return database_data_miRNA_in_results

In [6]:
def newMDA_in_database(new_MDA_simplied, database_data_miRNA_in_results):
    
    for i in trange(new_MDA_simplied.shape[0]):
        print('-------------------------{}-th new MDA--------------------------------------------'.format(i))
        miRNA = new_MDA_simplied.iloc[i]['miRNA_y']
        disease_of_miRNA = new_MDA_simplied.iloc[i]['disease_newMDA']
        print('miRNA = {}  ||  disease_of_miRNA = {}'.format(miRNA, disease_of_miRNA))
        disease_of_miRNA = disease_of_miRNA.split(' ')
        database_data_of_miRNA = database_data_miRNA_in_results[database_data_miRNA_in_results['miRNA'] == miRNA]
        
#         if disease_of_miRNA == '["Sjogren's Syndrome"]':
        for str_ in disease_of_miRNA:
            if str_ == '["Sjogren\'s': 
                str_ = 'Sjogren'
            if str_ == '["Sarcoma,':
                str_ = 'Sarcoma'
            if str_ == 'Ewing\'s"]':
                str_ = 'Ewing'
#             print(str_, disease_of_miRNA, type(disease_of_miRNA))
            res = database_data_of_miRNA.loc[database_data_of_miRNA['disease'].str.contains(str_)]
            print(str_, '--> ', res.values, '\n')

In [7]:
def run(task, database_data):
    results = pd.read_csv(task + '_unbalanced_case_study_0.csv', index_col = 0)
    new_MDA_origin, new_MDA_simplied = new_MDA(results, task, False)
    database_data_miRNA_in_results = database_data_miRNA_in_newMDA_results(database_data, new_MDA_simplied)
    newMDA_in_database(new_MDA_simplied, database_data_miRNA_in_results)
    return results, new_MDA, new_MDA_simplied, database_data_miRNA_in_results

In [34]:
results_Tp, new_MDA_Tp, new_MDA_simplied_Tp, database_data_miRNA_in_results_Tp = run(task = 'Tp', database_data = database_data)

/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
  0%|          | 9/3319 [00:00<00:40, 81.00it/s]

-------------------------0-th new MDA--------------------------------------------
miRNA = hsa-mir-126  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [['hsa-mir-126' nan 'Endocrine Gland Neoplasms' nan]] 

Injuries -->  [['hsa-mir-126' nan 'Spinal Cord Injuries' nan]
 ['hsa-mir-126' nan 'Vascular Injuries' nan]] 

-------------------------1-th new MDA--------------------------------------------
miRNA = hsa-mir-26b  ||  disease_of_miRNA = Waldenstrom Macroglobulinemia
Waldenstrom -->  [] 

Macroglobulinemia -->  [] 

-------------------------2-th new MDA--------------------------------------------
miRNA = hsa-mir-29a  ||  disease_of_miRNA = Waldenstrom Macroglobulinemia
Waldenstrom -->  [] 

Macroglobulinemia -->  [] 

-------------------------3-th new MDA--------------------------------------------
miRNA = hsa-mir-19b  ||  disease_of_miRNA = Vascular Diseases
Vascular -->  [] 

Diseases -->  [['hsa-mir-19b' nan 'Cardiovascular Diseases [unspecific]' nan]
 ['hsa-mi

  1%|          | 24/3319 [00:00<00:43, 75.54it/s]

Uterine -->  [] 

Cervical -->  [['hsa-mir-146b' nan 'Cervical Neoplasms' nan]] 

Neoplasms -->  [['hsa-mir-146b' nan 'Thyroid Neoplasms' nan]
 ['hsa-mir-146b' nan 'Prostate Neoplasms' nan]
 ['hsa-mir-146b' nan 'Breast Neoplasms' nan]
 ['hsa-mir-146b' nan 'Ovarian Neoplasms' nan]
 ['hsa-mir-146b' nan 'Lung Neoplasms' nan]
 ['hsa-mir-146b' nan 'Cervical Neoplasms' nan]
 ['hsa-mir-146b' nan 'Neoplasms [unspecific]' nan]
 ['hsa-mir-146b' nan 'Pancreatic Neoplasms' nan]
 ['hsa-mir-146b' nan 'Gastric Neoplasms' nan]
 ['hsa-mir-146b' nan 'Gastrointestinal Neoplasms' nan]
 ['hsa-mir-146b' nan 'Head And Neck Neoplasms' nan]
 ['hsa-mir-146b' nan 'Endometrial Neoplasms' nan]
 ['hsa-mir-146b' nan 'Bladder Neoplasms' nan]
 ['hsa-mir-146b' nan 'Myeloproliferative Neoplasms' nan]
 ['hsa-mir-146b' nan 'Endocrine Gland Neoplasms' nan]
 ['hsa-mir-146b' nan 'Prostatic Neoplasms' nan]
 ['hsa-mir-146b' nan 'Head and Neck Neoplasms' nan]
 ['hsa-mir-146b' nan 'Colorectal Neoplasms' nan]
 ['hsa-mir-146b' nan

  2%|▏         | 50/3319 [00:00<00:34, 95.33it/s]

...

Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3229-th new MDA--------------------------------------------
miRNA = hsa-mir-34b  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3230-th new MDA--------------------------------------------
miRNA = hsa-mir-339  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3231-th new MDA--------------------------------------------
miRNA = hsa-mir-214  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3232-th new MDA--------------------------------------------
miRNA = hsa-mir-142  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3233-th new MDA--------------------------------------------
miRNA = hsa-mir-29b  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae --

 99%|█████████▊| 3277/3319 [00:26<00:00, 142.24it/s]


Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3255-th new MDA--------------------------------------------
miRNA = hsa-mir-132  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3256-th new MDA--------------------------------------------
miRNA = hsa-mir-372  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3257-th new MDA--------------------------------------------
miRNA = hsa-mir-32  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [['hsa-mir-32' nan 'RNA Virus Infections' nan]] 

-------------------------3258-th new MDA--------------------------------------------
miRNA = hsa-mir-320a  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3259-th new MDA--------------------------------------------
miRNA = hsa-mir-153  ||  disease_of_m

100%|██████████| 3319/3319 [00:26<00:00, 123.18it/s]

Adenocarcinoma -->  [] 

-------------------------3292-th new MDA--------------------------------------------
miRNA = hsa-let-7b  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [['hsa-let-7b' nan 'Rectum Adenocarcinoma' nan]
 ['hsa-let-7b' nan 'Adenocarcinoma, Lung' nan]] 

-------------------------3293-th new MDA--------------------------------------------
miRNA = hsa-mir-125a  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [['hsa-mir-125a' nan 'Adenocarcinoma, Esophageal' nan]] 

-------------------------3294-th new MDA--------------------------------------------
miRNA = hsa-mir-218  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [['hsa-mir-218' nan 'Adenocarcinoma, Colon' nan]
 ['hsa-mir-218' nan 'Adenocarcinoma, Pancreatic Ductal' nan]
 ['hsa-mir-218' nan 'Adenocarcinoma, Lung' nan]] 

-------------------------3295-th new MDA--------------------------------------------
miRNA = hsa-mir-302d  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [

In [8]:
results_Tm, new_MDA_Tm, new_MDA_simplied_Tm, database_data_miRNA_in_results_Tm = run(task = 'Tm', database_data = database_data)

/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
  0%|          | 8/3606 [00:00<00:46, 77.82it/s]

-------------------------0-th new MDA--------------------------------------------
miRNA = hsa-mir-208a  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [] 

Injuries -->  [] 

-------------------------1-th new MDA--------------------------------------------
miRNA = hsa-mir-125b  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [['hsa-mir-125b' nan 'Squamous Cell Carcinoma, Head and Neck' nan]] 

Injuries -->  [['hsa-mir-125b' nan 'Spinal Cord Injuries' nan]] 

-------------------------2-th new MDA--------------------------------------------
miRNA = hsa-mir-199a  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [] 

Injuries -->  [['hsa-mir-199a' nan 'Spinal Cord Injuries' nan]] 

-------------------------3-th new MDA--------------------------------------------
miRNA = hsa-mir-29c  ||  disease_of_miRNA = Waldenstrom Macroglobulinemia
Waldenstrom -->  [] 

Macroglobulinemia -->  [] 

-------------------------4-th new MDA-------

  1%|          | 22/3606 [00:00<00:51, 69.30it/s]

Vascular -->  [['hsa-mir-129' nan 'Vascular Injuries' nan]] 

Diseases -->  [['hsa-mir-129' nan 'Inflammatory Bowel Diseases' nan]
 ['hsa-mir-129' nan 'Cardiovascular Diseases [unspecific]' nan]] 

-------------------------16-th new MDA--------------------------------------------
miRNA = hsa-mir-219  ||  disease_of_miRNA = Uterine Cervical Neoplasms
Uterine -->  [] 

Cervical -->  [] 

Neoplasms -->  [['hsa-mir-219' nan 'Breast Neoplasms' nan]
 ['hsa-mir-219' nan 'Neoplasms [unspecific]' nan]] 

-------------------------17-th new MDA--------------------------------------------
miRNA = hsa-mir-210  ||  disease_of_miRNA = Uterine Cervical Neoplasms
Uterine -->  [] 

Cervical -->  [['hsa-mir-210' nan 'Cervical Neoplasms' nan]
 ['hsa-mir-210' nan 'Carcinoma, Cervical' nan]] 

Neoplasms -->  [['hsa-mir-210' nan 'Breast Neoplasms' nan]
 ['hsa-mir-210' nan 'Prostate Neoplasms' nan]
 ['hsa-mir-210' nan 'Adrenal Cortex Neoplasms' nan]
 ['hsa-mir-210' nan 'Gastric Neoplasms' nan]
 ['hsa-mir-210'

  1%|          | 39/3606 [00:00<00:47, 74.39it/s]

...

Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3517-th new MDA--------------------------------------------
miRNA = hsa-mir-198  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3518-th new MDA--------------------------------------------
miRNA = hsa-mir-296  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3519-th new MDA--------------------------------------------
miRNA = hsa-mir-107  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3520-th new MDA--------------------------------------------
miRNA = hsa-mir-373  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -->  [] 

Infections -->  [] 

-------------------------3521-th new MDA--------------------------------------------
miRNA = hsa-mir-199b  ||  disease_of_miRNA = Adenoviridae Infections
Adenoviridae -

 99%|█████████▉| 3578/3606 [00:34<00:00, 142.93it/s]

Adenocarcinoma -->  [['hsa-let-7b' nan 'Rectum Adenocarcinoma' nan]
 ['hsa-let-7b' nan 'Adenocarcinoma, Lung' nan]] 

-------------------------3549-th new MDA--------------------------------------------
miRNA = hsa-mir-29b  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [['hsa-mir-29b' nan 'Adenocarcinoma, Lung' nan]] 

-------------------------3550-th new MDA--------------------------------------------
miRNA = hsa-mir-137  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [] 

-------------------------3551-th new MDA--------------------------------------------
miRNA = hsa-mir-199a  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [['hsa-mir-199a' nan 'Adenocarcinoma, Pancreatic Ductal' nan]] 

-------------------------3552-th new MDA--------------------------------------------
miRNA = hsa-mir-125a  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [['hsa-mir-125a' nan 'Adenocarcinoma, Esophageal' nan]] 

-------------------------3553-th new MDA-----

100%|██████████| 3606/3606 [00:34<00:00, 103.74it/s]


Adenocarcinoma -->  [['hsa-let-7g' nan 'Adenocarcinoma, Lung' nan]] 

-------------------------3586-th new MDA--------------------------------------------
miRNA = hsa-mir-153  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [['hsa-mir-153' nan 'Adenocarcinoma, Pancreatic Ductal' nan]
 ['hsa-mir-153' nan 'Adenocarcinoma, Lung' nan]] 

-------------------------3587-th new MDA--------------------------------------------
miRNA = hsa-mir-148b  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [] 

-------------------------3588-th new MDA--------------------------------------------
miRNA = hsa-mir-133b  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [] 

-------------------------3589-th new MDA--------------------------------------------
miRNA = hsa-mir-107  ||  disease_of_miRNA = Adenocarcinoma
Adenocarcinoma -->  [['hsa-mir-107' nan 'Adenocarcinoma, Gastric' nan]
 ['hsa-mir-107' nan 'Adenocarcinoma, Pancreatic Ductal' nan]
 ['hsa-mir-107' nan 'Adenocarcinoma, C

In [10]:
results_Td, new_MDA_Td, new_MDA_simplied_Td, database_data_miRNA_in_results_Td = run(task = 'Td', database_data = database_data)

/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
  0%|          | 4/8092 [00:00<03:29, 38.61it/s]

-------------------------0-th new MDA--------------------------------------------
miRNA = hsa-mir-141  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [['hsa-mir-141' nan 'Squamous Cell Carcinoma, Head and Neck' nan]
 ['hsa-mir-141' nan 'Endocrine Gland Neoplasms' nan]
 ['hsa-mir-141' nan 'Head and Neck Neoplasms' nan]] 

Injuries -->  [] 

-------------------------1-th new MDA--------------------------------------------
miRNA = hsa-mir-572  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [] 

Injuries -->  [] 

-------------------------2-th new MDA--------------------------------------------
miRNA = hsa-mir-642a  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [] 

Injuries -->  [] 

-------------------------3-th new MDA--------------------------------------------
miRNA = hsa-mir-16  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [['hsa-mir-16' nan 'Squamous Cell Carcinoma, Head and Neck' nan]
 ['hsa-

  0%|          | 14/8092 [00:00<03:27, 38.84it/s]

Injuries -->  [] 

-------------------------7-th new MDA--------------------------------------------
miRNA = hsa-mir-627  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [] 

Injuries -->  [] 

-------------------------8-th new MDA--------------------------------------------
miRNA = hsa-mir-552  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [] 

Injuries -->  [] 

-------------------------9-th new MDA--------------------------------------------
miRNA = hsa-mir-33b  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [] 

Injuries -->  [] 

-------------------------10-th new MDA--------------------------------------------
miRNA = hsa-mir-431  ||  disease_of_miRNA = Wounds and Injuries
Wounds -->  [] 

and -->  [['hsa-mir-431' nan 'Squamous Cell Carcinoma, Head and Neck' nan]] 

Injuries -->  [] 

-------------------------11-th new MDA--------------------------------------------
miRNA = hsa-mir-224  ||  disease_of_miRNA = Wound

  0%|          | 25/8092 [00:00<03:04, 43.64it/s]

...

Acquired -->  [] 

Immunodeficiency -->  [] 

Syndrome -->  [['hsa-mir-145' nan 'Myelodysplastic Syndromes' nan]
 ['hsa-mir-145' nan 'Chromosome 5q Deletion Syndrome' nan]
 ['hsa-mir-145' nan 'Polycystic Ovarian Syndrome' nan]
 ['hsa-mir-145' nan 'Irritable Bowel Syndrome' nan]] 

-------------------------8062-th new MDA--------------------------------------------
miRNA = hsa-mir-373  ||  disease_of_miRNA = Acquired Immunodeficiency Syndrome
Acquired -->  [] 

Immunodeficiency -->  [] 

Syndrome -->  [] 

-------------------------8063-th new MDA--------------------------------------------
miRNA = hsa-mir-488  ||  disease_of_miRNA = Acquired Immunodeficiency Syndrome
Acquired -->  [] 

Immunodeficiency -->  [] 

Syndrome -->  [] 

-------------------------8064-th new MDA--------------------------------------------
miRNA = hsa-mir-595  ||  disease_of_miRNA = Acquired Immunodeficiency Syndrome
Acquired -->  [] 

Immunodeficiency -->  [] 

Syndrome -->  [] 

-------------------------8065-t

100%|█████████▉| 8084/8092 [01:25<00:00, 54.83it/s]

 

Habitual -->  [] 

-------------------------8073-th new MDA--------------------------------------------
miRNA = hsa-mir-548b  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8074-th new MDA--------------------------------------------
miRNA = hsa-mir-378f  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8075-th new MDA--------------------------------------------
miRNA = hsa-mir-1231  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8076-th new MDA--------------------------------------------
miRNA = hsa-mir-365a  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8077-th new MDA--------------------------------------------
miRNA = hsa-mir-101  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8078-th new MD

100%|██████████| 8092/8092 [01:26<00:00, 94.04it/s]

 -->  [] 

-------------------------8085-th new MDA--------------------------------------------
miRNA = hsa-mir-297  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8086-th new MDA--------------------------------------------
miRNA = hsa-mir-500a  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8087-th new MDA--------------------------------------------
miRNA = hsa-mir-1207  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8088-th new MDA--------------------------------------------
miRNA = hsa-mir-648  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8089-th new MDA--------------------------------------------
miRNA = hsa-mir-99a  ||  disease_of_miRNA = Abortion, Habitual
Abortion, -->  [] 

Habitual -->  [] 

-------------------------8090-th new MDA------------

# 整理

In [11]:
def process_results(results):
    temp = []
    for item in results['disease_y'].tolist():
        item = item.replace("['",'').replace("']", "")
        temp.append(item)
    results['disease'] = temp
    return results

In [16]:
def metrics(y_true, y_pred, y_prob):

    tn, fp, fn, tp = confusion_matrix(y_true, y_pred).ravel()

    pos_acc = tp / sum(y_true)
    neg_acc = tn / (len(y_pred) - sum(y_pred)) # [y_true=0 & y_pred=0] / y_pred=0
    accuracy = (tp+tn)/(tn+fp+fn+tp)
    
    recall = tp / (tp+fn)
    precision = tp / (tp+fp)
    f1 = 2*precision*recall / (precision+recall)
    
    roc_auc = roc_auc_score(y_true, y_prob)
    prec, reca, _ = precision_recall_curve(y_true, y_prob)
    aupr = auc(reca, prec)
    average1 = (accuracy + precision + recall + roc_auc + aupr) / 5
    average2 = (accuracy + f1 + roc_auc + aupr) / 4
    average3 = (f1 + aupr) / 2
    print('tn = {}, fp = {}, fn = {}, tp = {}'.format(tn, fp, fn, tp))
    print('y_pred: 0 = {} | 1 = {}'.format(Counter(y_pred)[0], Counter(y_pred)[1]))
    print('y_true: 0 = {} | 1 = {}'.format(Counter(y_true)[0], Counter(y_true)[1]))
    print('acc={:.4f}|precision={:.4f}|recall={:.4f}|f1={:.4f}|auc={:.4f}|aupr={:.4f}|pos_acc={:.4f}|neg_acc={:.4f}'.format(accuracy, precision, recall, f1, roc_auc, aupr, pos_acc, neg_acc))
    print('{:.4f}, {:.4f}, {:.4f}, {:.4f}, {:.4f}, {:.4f}, {:.4f}, {:.4f}, {:.4f}'.format(accuracy, precision, recall, f1, roc_auc, aupr, average1, average2, average3))

In [13]:
def obtain_metrics(results_specific_disease):
    y_true = np.array(results_specific_disease['y_true'])
    y_pred = np.array(results_specific_disease['y_pred'])
    y_prob = np.array(results_specific_disease['y_prob'])
    metrics(y_true, y_pred, y_prob)

In [35]:
results_Tp = process_results(results_Tp)
results_Tp 

miRNA_x  disease_x  y_true  y_pred    y_prob       miRNA_y  \
155938       14        383     1.0     1.0  0.999916    hsa-mir-21   
155948       24        383     0.0     1.0  0.997668   hsa-mir-126   
155934       10        383     1.0     1.0  0.708075   hsa-mir-145   
155947       23        383     0.0     0.0  0.268306   hsa-mir-10b   
156343      419        383     0.0     0.0  0.197201   hsa-mir-641   
...         ...        ...     ...     ...       ...           ...   
35953       314          1     0.0     0.0  0.000004   hsa-mir-330   
35908       269          1     0.0     0.0  0.000004  hsa-mir-526a   
35808       169          1     0.0     0.0  0.000004   hsa-mir-497   
36022       383          1     0.0     0.0  0.000003  hsa-mir-520g   
35966       327          1     0.0     0.0  0.000003   hsa-mir-512   

                      disease_y              disease  
155938  ['Wounds and Injuries']  Wounds and Injuries  
155948  ['Wounds and Injuries']  Wounds and Injuries  
155934  ['Wounds and Injuries']  Wounds and Injuries  
155947  ['Wounds and Injuries']  Wounds and Injuries  
156343  ['Wounds and Injuries']  Wounds and Injuries  
...                         ...                  ...  
35953    ['Abortion, Habitual']   Abortion, Habitual  
35908    ['Abortion, Habitual']   Abortion, Habitual  
35808    ['Abortion, Habitual']   Abortion, Habitual  
36022    ['Abortion, Habitual']   Abortion, Habitual  
35966    ['Abortion, Habitual']   Abortion, Habitual  

[189585 rows x 8 columns]

In [36]:
results_Tm = process_results(results_Tm)
results_Tm 

miRNA_x  disease_x  y_true  y_pred        y_prob       miRNA_y  \
76649      308        383     0.0     1.0  6.435882e-01  hsa-mir-208a   
76272       65        383     0.0     1.0  5.558605e-01  hsa-mir-125b   
76542      138        383     0.0     1.0  5.408920e-01  hsa-mir-199a   
76628       47        383     0.0     0.0  4.035085e-01   hsa-mir-223   
76265       29        383     0.0     0.0  3.324498e-01  hsa-mir-181b   
...        ...        ...     ...     ...           ...           ...   
70028      212          1     0.0     0.0  1.406977e-07  hsa-mir-1471   
70078      302          1     0.0     0.0  1.170808e-07  hsa-mir-1271   
70084      385          1     0.0     0.0  1.085159e-07   hsa-mir-873   
70015      107          1     0.0     0.0  1.038046e-07   hsa-mir-744   
70061      449          1     0.0     0.0  9.520525e-08   hsa-mir-769   

                     disease_y              disease  
76649  ['Wounds and Injuries']  Wounds and Injuries  
76272  ['Wounds and Injuries']  Wounds and Injuries  
76542  ['Wounds and Injuries']  Wounds and Injuries  
76628  ['Wounds and Injuries']  Wounds and Injuries  
76265  ['Wounds and Injuries']  Wounds and Injuries  
...                        ...                  ...  
70028   ['Abortion, Habitual']   Abortion, Habitual  
70078   ['Abortion, Habitual']   Abortion, Habitual  
70084   ['Abortion, Habitual']   Abortion, Habitual  
70015   ['Abortion, Habitual']   Abortion, Habitual  
70061   ['Abortion, Habitual']   Abortion, Habitual  

[189585 rows x 8 columns]

In [12]:
results_Td = process_results(results_Td)
results_Td 

miRNA_x  disease_x  y_true  y_pred    y_prob       miRNA_y  \
129262      488        383     1.0     1.0  0.881445   hsa-mir-938   
129261      176        383     1.0     1.0  0.881387  hsa-mir-193a   
129683      389        383     1.0     1.0  0.879987  hsa-mir-1322   
129655      120        383     1.0     1.0  0.879839  hsa-mir-106b   
129438       75        383     1.0     1.0  0.879612   hsa-mir-19b   
...         ...        ...     ...     ...       ...           ...   
134536      101          1     0.0     0.0  0.120544   hsa-mir-619   
134145      438          1     0.0     0.0  0.120346   hsa-mir-511   
134235      479          1     0.0     0.0  0.120238  hsa-mir-518f   
134275       68          1     0.0     0.0  0.120039  hsa-mir-146b   
134243       12          1     0.0     0.0  0.119149   hsa-mir-15a   

                      disease_y              disease  
129262  ['Wounds and Injuries']  Wounds and Injuries  
129261  ['Wounds and Injuries']  Wounds and Injuries  
129683  ['Wounds and Injuries']  Wounds and Injuries  
129655  ['Wounds and Injuries']  Wounds and Injuries  
129438  ['Wounds and Injuries']  Wounds and Injuries  
...                         ...                  ...  
134536   ['Abortion, Habitual']   Abortion, Habitual  
134145   ['Abortion, Habitual']   Abortion, Habitual  
134235   ['Abortion, Habitual']   Abortion, Habitual  
134275   ['Abortion, Habitual']   Abortion, Habitual  
134243   ['Abortion, Habitual']   Abortion, Habitual  

[189585 rows x 8 columns]

In [52]:
all_results = pd.concat([results_Tp, results_Tm], axis = 0)
all_results = pd.concat([all_results, results_Td], axis = 0)
all_results.sort_values(by = 'y_prob', ascending = False, inplace = True)
all_results.drop_duplicates(subset = ['miRNA_x', 'disease_x', 'y_true', 'miRNA_y', 'disease_y', 'disease'], keep = 'first', inplace = True)
obtain_metrics(all_results)
all_results

tn = 176156, fp = 13240, fn = 3445, tp = 7226
y_pred: 0 = 179601 | 1 = 20466
y_true: 0 = 189396 | 1 = 10671
acc=0.9166|precision=0.3531|recall=0.6772|f1=0.4641|auc=0.8292|aupr=0.4903|pos_acc=0.6772|neg_acc=0.9808
0.9166, 0.3531, 0.6772, 0.4641, 0.8292, 0.4903, 0.6533, 0.6751, 0.4772


miRNA_x  disease_x  y_true  y_pred    y_prob       miRNA_y  \
166079        7        110     1.0     1.0  0.999996    hsa-let-7a   
117586      164        349     1.0     1.0  0.999995    hsa-let-7i   
166035      118        110     1.0     1.0  0.999995    hsa-let-7c   
106640       17        163     1.0     1.0  0.999995  hsa-mir-133b   
165899      119        110     1.0     1.0  0.999995    hsa-let-7d   
...         ...        ...     ...     ...       ...           ...   
59712       313        245     0.0     0.0  0.000003  hsa-mir-323b   
111147      268        373     0.0     0.0  0.000003  hsa-mir-520h   
66575       246        308     0.0     0.0  0.000003   hsa-mir-423   
176849      135        256     0.0     0.0  0.000003   hsa-mir-424   
2175        196         20     0.0     0.0  0.000003  hsa-mir-520d   

                             disease_y                     disease  
166079  ['Digestive System Neoplasms']  Digestive System Neoplasms  
117586             ['Sarcoma, Kaposi']             Sarcoma, Kaposi  
166035  ['Digestive System Neoplasms']  Digestive System Neoplasms  
106640               ['Heart Failure']               Heart Failure  
165899  ['Digestive System Neoplasms']  Digestive System Neoplasms  
...                                ...                         ...  
59712        ['Lymphoma, Mantle-Cell']       Lymphoma, Mantle-Cell  
111147                  ['Toxoplasma']                  Toxoplasma  
66575               ['Panic Disorder']              Panic Disorder  
176849          ['Metabolic Diseases']          Metabolic Diseases  
2175              ['Angina, Unstable']            Angina, Unstable  

[200067 rows x 8 columns]

In [21]:
neoplasm_diseases = list(set(results_Td.loc[results_Td['disease'].str.contains('Neoplasms')]['disease']))
neoplasm_diseases

['Salivary Gland Neoplasms',
 'Gastrointestinal Neoplasms',
 'Cerebellar Neoplasms',
 'Breast Neoplasms',
 'Lung Neoplasms',
 'Colon Neoplasms',
 'Mouth Neoplasms',
 'Neoplasms, Germ Cell and Embryonal',
 'Colonic Neoplasms',
 'Nasopharyngeal Neoplasms',
 'Nerve Sheath Neoplasms',
 'Esophageal Neoplasms',
 'Gastric Neoplasms',
 'Biliary Tract Neoplasms',
 'Stomach Neoplasms',
 'Endometrial Neoplasms',
 'Brain Neoplasms',
 'Liver Neoplasms',
 'Tongue Neoplasms',
 'Digestive System Neoplasms',
 'Skin Neoplasms',
 'Laryngeal Neoplasms',
 'Colorectal Neoplasms, Hereditary Nonpolyposis',
 'Adrenal Cortex Neoplasms',
 'Ovarian Neoplasms',
 'Uterine Cervical Neoplasms',
 'Anus Neoplasms',
 'Stomach Neoplasms ',
 'Kidney Neoplasms',
 'Urinary Bladder Neoplasms',
 'Colorectal Neoplasms',
 'Rectal Neoplasms',
 'Bladder Neoplasms',
 'Neoplasms',
 'Hematologic Neoplasms',
 'Testicular Neoplasms',
 'Pancreatic Neoplasms',
 'Cervical Neoplasms',
 'Prostatic Neoplasms',
 'Prostate Neoplasms',
 'Hypop

In [32]:
notepad_search = []
for item in neoplasm_diseases:
    notepad_search.append(" = " + item + ".* Neoplasms\r\n" + item + ".* -->  \[\[")
notepad_search

[' = Salivary Gland Neoplasms.* Neoplasms\r\nSalivary Gland Neoplasms.* -->  \\[\\[',
 ' = Gastrointestinal Neoplasms.* Neoplasms\r\nGastrointestinal Neoplasms.* -->  \\[\\[',
 ' = Cerebellar Neoplasms.* Neoplasms\r\nCerebellar Neoplasms.* -->  \\[\\[',
 ' = Breast Neoplasms.* Neoplasms\r\nBreast Neoplasms.* -->  \\[\\[',
 ' = Lung Neoplasms.* Neoplasms\r\nLung Neoplasms.* -->  \\[\\[',
 ' = Colon Neoplasms.* Neoplasms\r\nColon Neoplasms.* -->  \\[\\[',
 ' = Mouth Neoplasms.* Neoplasms\r\nMouth Neoplasms.* -->  \\[\\[',
 ' = Neoplasms, Germ Cell and Embryonal.* Neoplasms\r\nNeoplasms, Germ Cell and Embryonal.* -->  \\[\\[',
 ' = Colonic Neoplasms.* Neoplasms\r\nColonic Neoplasms.* -->  \\[\\[',
 ' = Nasopharyngeal Neoplasms.* Neoplasms\r\nNasopharyngeal Neoplasms.* -->  \\[\\[',
 ' = Nerve Sheath Neoplasms.* Neoplasms\r\nNerve Sheath Neoplasms.* -->  \\[\\[',
 ' = Esophageal Neoplasms.* Neoplasms\r\nEsophageal Neoplasms.* -->  \\[\\[',
 ' = Gastric Neoplasms.* Neoplasms\r\nGastric Neop

# All

In [31]:
for idx, item in enumerate(neoplasm_diseases):
    print('===============================')
    print(idx, item)
    results_Td_item_neoplasm = results_Td.loc[results_Td['disease'].str.contains(item)]
    if results_Td_item_neoplasm.shape[0] != 0:
        obtain_metrics(results_Td_item_neoplasm)

0 Salivary Gland Neoplasms
tn = 461, fp = 19, fn = 4, tp = 11
y_pred: 0 = 465 | 1 = 30
y_true: 0 = 480 | 1 = 15
acc=0.9535|precision=0.3667|recall=0.7333|f1=0.4889|auc=0.9299|aupr=0.6099|pos_acc=0.7333|neg_acc=0.9914
0.9535, 0.3667, 0.7333, 0.4889, 0.9299, 0.6099, 0.7187, 0.7456, 0.5494
1 Gastrointestinal Neoplasms
tn = 464, fp = 15, fn = 5, tp = 11
y_pred: 0 = 469 | 1 = 26
y_true: 0 = 479 | 1 = 16
acc=0.9596|precision=0.4231|recall=0.6875|f1=0.5238|auc=0.9470|aupr=0.4487|pos_acc=0.6875|neg_acc=0.9893
0.9596, 0.4231, 0.6875, 0.5238, 0.9470, 0.4487, 0.6932, 0.7198, 0.4863
2 Cerebellar Neoplasms
tn = 459, fp = 18, fn = 10, tp = 8
y_pred: 0 = 469 | 1 = 26
y_true: 0 = 477 | 1 = 18
acc=0.9434|precision=0.3077|recall=0.4444|f1=0.3636|auc=0.8811|aupr=0.2801|pos_acc=0.4444|neg_acc=0.9787
0.9434, 0.3077, 0.4444, 0.3636, 0.8811, 0.2801, 0.5714, 0.6171, 0.3219
3 Breast Neoplasms
tn = 454, fp = 17, fn = 9, tp = 15
y_pred: 0 = 463 | 1 = 32
y_true: 0 = 471 | 1 = 24
acc=0.9475|precision=0.4688|recall

# Colon

In [98]:
# results_Td[results_Td['disease'] == 'Neoplasms']
results_Td_colon_neoplasm = results_Td.loc[results_Td['disease'].str.contains('Colon.* Neoplasms')]
obtain_metrics(results_Td_colon_neoplasm)
results_Td_colon_neoplasm

tn = 902, fp = 50, fn = 14, tp = 24
y_pred: 0 = 916 | 1 = 74
y_true: 0 = 952 | 1 = 38
acc=0.9354|precision=0.3243|recall=0.6316|f1=0.4286|auc=0.9275|aupr=0.3609|pos_acc=0.6316|neg_acc=0.9847
0.9354, 0.3243, 0.6316, 0.4286, 0.9275, 0.3609, 0.6359, 0.6631, 0.3947


miRNA_x  disease_x  y_true  y_pred    y_prob       miRNA_y  \
118095      330         92     1.0     1.0  0.882647  hsa-mir-518b   
118130       65         92     1.0     1.0  0.882214  hsa-mir-125b   
118094       37         92     1.0     1.0  0.881826  hsa-mir-200a   
118263      132         92     1.0     1.0  0.881785  hsa-mir-376a   
118082      201         92     1.0     1.0  0.881618   hsa-mir-326   
...         ...        ...     ...     ...       ...           ...   
84301       351         91     0.0     0.0  0.070352  hsa-mir-124a   
84615       406         91     0.0     0.0  0.069988   hsa-mir-545   
84388       254         91     0.0     0.0  0.069631   hsa-mir-493   
84245       422         91     0.0     0.0  0.069517   hsa-mir-384   
84256       229         91     0.0     0.0  0.068688   hsa-mir-299   

                    disease_y            disease  
118095  ['Colonic Neoplasms']  Colonic Neoplasms  
118130  ['Colonic Neoplasms']  Colonic Neoplasms  
118094  ['Colonic Neoplasms']  Colonic Neoplasms  
118263  ['Colonic Neoplasms']  Colonic Neoplasms  
118082  ['Colonic Neoplasms']  Colonic Neoplasms  
...                       ...                ...  
84301     ['Colon Neoplasms']    Colon Neoplasms  
84615     ['Colon Neoplasms']    Colon Neoplasms  
84388     ['Colon Neoplasms']    Colon Neoplasms  
84245     ['Colon Neoplasms']    Colon Neoplasms  
84256     ['Colon Neoplasms']    Colon Neoplasms  

[990 rows x 8 columns]

In [99]:
verified_colon = ['hsa-mir-125a'
,'hsa-let-7e'  
,'hsa-mir-32'  
,'hsa-mir-200b'
,'hsa-mir-506' 
,'hsa-mir-301b'
,'hsa-let-7d'  
,'hsa-mir-296' 
,'hsa-mir-96'  
,'hsa-mir-1297'
,'hsa-mir-26b' 
,'hsa-mir-22']

results_Td_colon_neoplasm['y_true'][results_Td_colon_neoplasm['miRNA_y'].isin(verified_colon)] = 1
obtain_metrics(results_Td_colon_neoplasm)

tn = 890, fp = 38, fn = 26, tp = 36
y_pred: 0 = 916 | 1 = 74
y_true: 0 = 928 | 1 = 62
acc=0.9354|precision=0.4865|recall=0.5806|f1=0.5294|auc=0.8507|aupr=0.3767|pos_acc=0.5806|neg_acc=0.9716
0.9354, 0.4865, 0.5806, 0.5294, 0.8507, 0.3767, 0.6460, 0.6730, 0.4530


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-

In [126]:
obtain_metrics(results_Td_colon_neoplasm.iloc[:62])

tn = 20, fp = 22, fn = 1, tp = 19
y_pred: 0 = 21 | 1 = 41
y_true: 0 = 42 | 1 = 20
acc=0.6290|precision=0.4634|recall=0.9500|f1=0.6230|auc=0.7810|aupr=0.6720|pos_acc=0.9500|neg_acc=0.9524
0.6290, 0.4634, 0.9500, 0.6230, 0.7810, 0.6720, 0.6991, 0.6762, 0.6475


# Breast

In [79]:
results_Td_breast_neoplasm = results_Td.loc[results_Td['disease'].str.contains('Breast.* Neoplasms')]
obtain_metrics(results_Td_breast_neoplasm)
results_Td_breast_neoplasm

tn = 454, fp = 17, fn = 9, tp = 15
y_pred: 0 = 463 | 1 = 32
y_true: 0 = 471 | 1 = 24
acc=0.9475|precision=0.4688|recall=0.6250|f1=0.5357|auc=0.9354|aupr=0.3781|pos_acc=0.6250|neg_acc=0.9806
0.9475, 0.4688, 0.6250, 0.5357, 0.9354, 0.3781, 0.6710, 0.6992, 0.4569


miRNA_x  disease_x  y_true  y_pred    y_prob       miRNA_y  \
144568      383         50     0.0     1.0  0.881080  hsa-mir-520g   
144611      328         50     1.0     1.0  0.878566  hsa-mir-517a   
144592      285         50     0.0     1.0  0.873334  hsa-mir-3196   
144939      105         50     1.0     1.0  0.873045   hsa-mir-655   
144889      273         50     1.0     1.0  0.872603   hsa-mir-629   
...         ...        ...     ...     ...       ...           ...   
144724      264         50     0.0     0.0  0.120349  hsa-mir-519e   
144558      347         50     0.0     0.0  0.120346  hsa-mir-3940   
144655       42         50     0.0     0.0  0.120053   hsa-mir-205   
144730      237         50     0.0     0.0  0.119674  hsa-mir-320e   
144557      320         50     0.0     0.0  0.118721   hsa-mir-490   

                   disease_y           disease  
144568  ['Breast Neoplasms']  Breast Neoplasms  
144611  ['Breast Neoplasms']  Breast Neoplasms  
144592  ['Breast Neoplasms']  Breast Neoplasms  
144939  ['Breast Neoplasms']  Breast Neoplasms  
144889  ['Breast Neoplasms']  Breast Neoplasms  
...                      ...               ...  
144724  ['Breast Neoplasms']  Breast Neoplasms  
144558  ['Breast Neoplasms']  Breast Neoplasms  
144655  ['Breast Neoplasms']  Breast Neoplasms  
144730  ['Breast Neoplasms']  Breast Neoplasms  
144557  ['Breast Neoplasms']  Breast Neoplasms  

[495 rows x 8 columns]

In [80]:
verified_breast = ['hsa-mir-520g'
                    ,'hsa-mir-3196'
                    ,'hsa-mir-127'
                    ,'hsa-mir-584'
                    ,'hsa-mir-489'
                    ,'hsa-mir-18a'
                    ,'hsa-mir-106a'
                    ,'hsa-mir-519d'
                    ,'hsa-mir-34c'
                    ,'hsa-mir-98'
                    ,'hsa-mir-25']
results_Td_breast_neoplasm['y_true'][results_Td_breast_neoplasm['miRNA_y'].isin(verified_breast)] = 1
obtain_metrics(results_Td_breast_neoplasm)

tn = 454, fp = 6, fn = 9, tp = 26
y_pred: 0 = 463 | 1 = 32
y_true: 0 = 460 | 1 = 35
acc=0.9697|precision=0.8125|recall=0.7429|f1=0.7761|auc=0.9637|aupr=0.7227|pos_acc=0.7429|neg_acc=0.9806
0.9697, 0.8125, 0.7429, 0.7761, 0.9637, 0.7227, 0.8423, 0.8580, 0.7494


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if sys.path[0] == '':
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/ind

In [162]:
results_Td_breast_neoplasm.sort_values(by = 'y_prob', ascending = False, inplace = True)
obtain_metrics(results_Td_breast_neoplasm.iloc[:35])

tn = 3, fp = 6, fn = 0, tp = 26
y_pred: 0 = 3 | 1 = 32
y_true: 0 = 9 | 1 = 26
acc=0.8286|precision=0.8125|recall=1.0000|f1=0.8966|auc=0.6282|aupr=0.8301|pos_acc=1.0000|neg_acc=1.0000
0.8286, 0.8125, 1.0000, 0.8966, 0.6282, 0.8301, 0.8199, 0.7959, 0.8633


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


# Kidney

In [82]:
results_Td_kidney_neoplasm = results_Td.loc[results_Td['disease'].str.contains('Kidney.* Neoplasms')]
obtain_metrics(results_Td_kidney_neoplasm)
results_Td_kidney_neoplasm

tn = 463, fp = 20, fn = 6, tp = 6
y_pred: 0 = 469 | 1 = 26
y_true: 0 = 483 | 1 = 12
acc=0.9475|precision=0.2308|recall=0.5000|f1=0.3158|auc=0.9044|aupr=0.4068|pos_acc=0.5000|neg_acc=0.9872
0.9475, 0.2308, 0.5000, 0.3158, 0.9044, 0.4068, 0.5979, 0.6436, 0.3613


miRNA_x  disease_x  y_true  y_pred    y_prob       miRNA_y  \
156243      308        205     1.0     1.0  0.839651  hsa-mir-208a   
156023       12        205     1.0     1.0  0.830683   hsa-mir-15a   
156302      250        205     0.0     1.0  0.804017  hsa-mir-450a   
155932      431        205     1.0     1.0  0.768445  hsa-mir-3151   
155963       50        205     1.0     1.0  0.737085    hsa-mir-31   
...         ...        ...     ...     ...       ...           ...   
156142       95        205     0.0     0.0  0.090666   hsa-mir-454   
156047      119        205     0.0     0.0  0.090635    hsa-let-7d   
156180      246        205     0.0     0.0  0.090634   hsa-mir-423   
156148      393        205     0.0     0.0  0.090444   hsa-mir-758   
155938      484        205     0.0     0.0  0.089759   hsa-mir-591   

                   disease_y           disease  
156243  ['Kidney Neoplasms']  Kidney Neoplasms  
156023  ['Kidney Neoplasms']  Kidney Neoplasms  
156302  ['Kidney Neoplasms']  Kidney Neoplasms  
155932  ['Kidney Neoplasms']  Kidney Neoplasms  
155963  ['Kidney Neoplasms']  Kidney Neoplasms  
...                      ...               ...  
156142  ['Kidney Neoplasms']  Kidney Neoplasms  
156047  ['Kidney Neoplasms']  Kidney Neoplasms  
156180  ['Kidney Neoplasms']  Kidney Neoplasms  
156148  ['Kidney Neoplasms']  Kidney Neoplasms  
155938  ['Kidney Neoplasms']  Kidney Neoplasms  

[495 rows x 8 columns]

In [84]:
verified_kidney = ['hsa-mir-155'
,'hsa-mir-204'
,'hsa-mir-26a'
,'hsa-mir-26b'
,'hsa-mir-146a']

results_Td_kidney_neoplasm['y_true'][results_Td_kidney_neoplasm['miRNA_y'].isin(verified_kidney)] = 1
obtain_metrics(results_Td_kidney_neoplasm)

tn = 463, fp = 15, fn = 6, tp = 11
y_pred: 0 = 469 | 1 = 26
y_true: 0 = 478 | 1 = 17
acc=0.9576|precision=0.4231|recall=0.6471|f1=0.5116|auc=0.9322|aupr=0.5193|pos_acc=0.6471|neg_acc=0.9872
0.9576, 0.4231, 0.6471, 0.5116, 0.9322, 0.5193, 0.6958, 0.7302, 0.5155


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#r

In [119]:
obtain_metrics(results_Td_kidney_neoplasm.iloc[:17])

tn = 0, fp = 8, fn = 0, tp = 9
y_pred: 0 = 0 | 1 = 17
y_true: 0 = 8 | 1 = 9
acc=0.5294|precision=0.5294|recall=1.0000|f1=0.6923|auc=0.7361|aupr=0.7709|pos_acc=1.0000|neg_acc=nan
0.5294, 0.5294, 1.0000, 0.6923, 0.7361, 0.7709, 0.7132, 0.6822, 0.7316


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:6: RuntimeWarning: invalid value encountered in true_divide
  


# Prostate

In [85]:
results_Td_prostate_neoplasm = results_Td.loc[results_Td['disease'].str.contains('Prostat.* Neoplasms')]
obtain_metrics(results_Td_prostate_neoplasm)
results_Td_prostate_neoplasm

tn = 917, fp = 49, fn = 13, tp = 11
y_pred: 0 = 930 | 1 = 60
y_true: 0 = 966 | 1 = 24
acc=0.9374|precision=0.1833|recall=0.4583|f1=0.2619|auc=0.8289|aupr=0.2294|pos_acc=0.4583|neg_acc=0.9860
0.9374, 0.1833, 0.4583, 0.2619, 0.8289, 0.2294, 0.5275, 0.5644, 0.2456


miRNA_x  disease_x  y_true  y_pred    y_prob       miRNA_y  \
10525       68        328     1.0     1.0  0.850892  hsa-mir-146b   
10837      187        328     1.0     1.0  0.850887  hsa-mir-550a   
10814      446        328     0.0     1.0  0.846394   hsa-mir-654   
10658      183        328     0.0     1.0  0.845426   hsa-mir-381   
10527       40        328     0.0     1.0  0.843549   hsa-mir-203   
...        ...        ...     ...     ...       ...           ...   
55552      392        327     0.0     0.0  0.010148   hsa-mir-617   
55556      346        327     0.0     0.0  0.010118   hsa-mir-337   
55755      144        327     0.0     0.0  0.010077   hsa-mir-153   
55753      373        327     0.0     0.0  0.010065  hsa-mir-216b   
55924       63        327     0.0     0.0  0.009992  hsa-mir-1246   

                     disease_y              disease  
10525  ['Prostatic Neoplasms']  Prostatic Neoplasms  
10837  ['Prostatic Neoplasms']  Prostatic Neoplasms  
10814  ['Prostatic Neoplasms']  Prostatic Neoplasms  
10658  ['Prostatic Neoplasms']  Prostatic Neoplasms  
10527  ['Prostatic Neoplasms']  Prostatic Neoplasms  
...                        ...                  ...  
55552   ['Prostate Neoplasms']   Prostate Neoplasms  
55556   ['Prostate Neoplasms']   Prostate Neoplasms  
55755   ['Prostate Neoplasms']   Prostate Neoplasms  
55753   ['Prostate Neoplasms']   Prostate Neoplasms  
55924   ['Prostate Neoplasms']   Prostate Neoplasms  

[990 rows x 8 columns]

In [95]:
verified_prostate = ['hsa-mir-210'
,'hsa-mir-324' 
,'hsa-mir-331'
,'hsa-mir-1256'
,'hsa-mir-378h'
,'hsa-mir-203' 
,'hsa-mir-130b'
,'hsa-mir-320a']

results_Td_prostate_neoplasm['y_true'][results_Td_prostate_neoplasm['miRNA_y'].isin(verified_prostate)] = 1
obtain_metrics(results_Td_prostate_neoplasm)

tn = 909, fp = 41, fn = 21, tp = 19
y_pred: 0 = 930 | 1 = 60
y_true: 0 = 950 | 1 = 40
acc=0.9374|precision=0.3167|recall=0.4750|f1=0.3800|auc=0.8015|aupr=0.2761|pos_acc=0.4750|neg_acc=0.9774
0.9374, 0.3167, 0.4750, 0.3800, 0.8015, 0.2761, 0.5613, 0.5988, 0.3281


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pan

In [124]:
obtain_metrics(results_Td_prostate_neoplasm.iloc[:40])

tn = 3, fp = 25, fn = 2, tp = 10
y_pred: 0 = 5 | 1 = 35
y_true: 0 = 28 | 1 = 12
acc=0.3250|precision=0.2857|recall=0.8333|f1=0.4255|auc=0.6220|aupr=0.5087|pos_acc=0.8333|neg_acc=0.6000
0.3250, 0.2857, 0.8333, 0.4255, 0.6220, 0.5087, 0.5150, 0.4703, 0.4671


In [123]:
# obtain_metrics(results_Td_prostate_neoplasm[results_Td_prostate_neoplasm['y_pred'] == 1].iloc[:15])

# Colorectal

In [86]:
results_Td_colorectal_neoplasm = results_Td.loc[results_Td['disease'].str.contains('Color.* Neoplasms')]
obtain_metrics(results_Td_colorectal_neoplasm)
results_Td_colorectal_neoplasm

tn = 917, fp = 45, fn = 13, tp = 15
y_pred: 0 = 930 | 1 = 60
y_true: 0 = 962 | 1 = 28
acc=0.9414|precision=0.2500|recall=0.5357|f1=0.3409|auc=0.9020|aupr=0.3113|pos_acc=0.5357|neg_acc=0.9860
0.9414, 0.2500, 0.5357, 0.3409, 0.9020, 0.3113, 0.5881, 0.6239, 0.3261


miRNA_x  disease_x  y_true  y_pred    y_prob       miRNA_y  \
7983        407         94     0.0     1.0  0.851006   hsa-mir-628   
8388        236         94     0.0     1.0  0.846926  hsa-mir-320d   
8310         76         94     0.0     1.0  0.845439   hsa-mir-219   
8387        429         94     0.0     1.0  0.844153   hsa-mir-369   
8291        325         94     1.0     1.0  0.842346   hsa-mir-502   
...         ...        ...     ...     ...       ...           ...   
140813      113         93     0.0     0.0  0.119874   hsa-mir-99a   
140824      102         93     0.0     0.0  0.119718   hsa-mir-627   
140749       19         93     0.0     0.0  0.119616   hsa-mir-155   
140940      331         93     0.0     0.0  0.119279  hsa-mir-520e   
140972      482         93     0.0     0.0  0.117455   hsa-mir-570   

                                                disease_y  \
7983    ['Colorectal Neoplasms, Hereditary Nonpolyposis']   
8388    ['Colorectal Neoplasms, Hereditary Nonpolyposis']   
8310    ['Colorectal Neoplasms, Hereditary Nonpolyposis']   
8387    ['Colorectal Neoplasms, Hereditary Nonpolyposis']   
8291    ['Colorectal Neoplasms, Hereditary Nonpolyposis']   
...                                                   ...   
140813                           ['Colorectal Neoplasms']   
140824                           ['Colorectal Neoplasms']   
140749                           ['Colorectal Neoplasms']   
140940                           ['Colorectal Neoplasms']   
140972                           ['Colorectal Neoplasms']   

                                              disease  
7983    Colorectal Neoplasms, Hereditary Nonpolyposis  
8388    Colorectal Neoplasms, Hereditary Nonpolyposis  
8310    Colorectal Neoplasms, Hereditary Nonpolyposis  
8387    Colorectal Neoplasms, Hereditary Nonpolyposis  
8291    Colorectal Neoplasms, Hereditary Nonpolyposis  
...                                               ...  
140813                           Colorectal Neoplasms  
140824                           Colorectal Neoplasms  
140749                           Colorectal Neoplasms  
140940                           Colorectal Neoplasms  
140972                           Colorectal Neoplasms  

[990 rows x 8 columns]

In [96]:
verified_colorectal = ['hsa-mir-21'  
,'hsa-mir-567' 
,'hsa-mir-601' 
,'hsa-mir-630' 
,'hsa-mir-369' 
,'hsa-mir-147b'
,'hsa-mir-126' 
,'hsa-mir-205' 
,'hsa-mir-320a'
,'hsa-mir-603' 
,'hsa-mir-198' 
,'hsa-mir-92a' 
,'hsa-mir-17'  
,'hsa-mir-29c' 
,'hsa-mir-328' 
,'hsa-mir-574']

results_Td_colorectal_neoplasm['y_true'][results_Td_colorectal_neoplasm['miRNA_y'].isin(verified_colorectal)] = 1
obtain_metrics(results_Td_colorectal_neoplasm)

tn = 904, fp = 28, fn = 26, tp = 32
y_pred: 0 = 930 | 1 = 60
y_true: 0 = 932 | 1 = 58
acc=0.9455|precision=0.5333|recall=0.5517|f1=0.5424|auc=0.8782|aupr=0.5262|pos_acc=0.5517|neg_acc=0.9720
0.9455, 0.5333, 0.5517, 0.5424, 0.8782, 0.5262, 0.6870, 0.7231, 0.5343


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-v

In [120]:
obtain_metrics(results_Td_colorectal_neoplasm.iloc[:58])

tn = 27, fp = 20, fn = 4, tp = 7
y_pred: 0 = 31 | 1 = 27
y_true: 0 = 47 | 1 = 11
acc=0.5862|precision=0.2593|recall=0.6364|f1=0.3684|auc=0.6383|aupr=0.2823|pos_acc=0.6364|neg_acc=0.8710
0.5862, 0.2593, 0.6364, 0.3684, 0.6383, 0.2823, 0.4805, 0.4688, 0.3254


In [122]:
# obtain_metrics(results_Td_colorectal_neoplasm[results_Td_colorectal_neoplasm['y_pred'] == 1].iloc[:58])

# Lung

In [87]:
results_Td_lung_neoplasm = results_Td.loc[results_Td['disease'].str.contains('Lung.* Neoplasms')]
obtain_metrics(results_Td_lung_neoplasm)
results_Td_lung_neoplasm

tn = 458, fp = 24, fn = 4, tp = 9
y_pred: 0 = 462 | 1 = 33
y_true: 0 = 482 | 1 = 13
acc=0.9434|precision=0.2727|recall=0.6923|f1=0.3913|auc=0.9263|aupr=0.2702|pos_acc=0.6923|neg_acc=0.9913
0.9434, 0.2727, 0.6923, 0.3913, 0.9263, 0.2702, 0.6210, 0.6328, 0.3308


miRNA_x  disease_x  y_true  y_pred    y_prob       miRNA_y  \
141458      252        236     0.0     1.0  0.881766  hsa-mir-451a   
141206      189        236     0.0     1.0  0.880870   hsa-mir-652   
141267       83        236     1.0     1.0  0.880382   hsa-mir-324   
141383      284        236     1.0     1.0  0.880240  hsa-mir-2861   
141117      213        236     0.0     1.0  0.877080  hsa-mir-147a   
...         ...        ...     ...     ...       ...           ...   
141531       13        236     0.0     0.0  0.120433    hsa-mir-16   
141412      238        236     0.0     0.0  0.120284   hsa-mir-339   
141111      180        236     0.0     0.0  0.120274   hsa-mir-129   
141353       24        236     0.0     0.0  0.120003   hsa-mir-126   
141314      403        236     0.0     0.0  0.118538  hsa-mir-544b   

                 disease_y         disease  
141458  ['Lung Neoplasms']  Lung Neoplasms  
141206  ['Lung Neoplasms']  Lung Neoplasms  
141267  ['Lung Neoplasms']  Lung Neoplasms  
141383  ['Lung Neoplasms']  Lung Neoplasms  
141117  ['Lung Neoplasms']  Lung Neoplasms  
...                    ...             ...  
141531  ['Lung Neoplasms']  Lung Neoplasms  
141412  ['Lung Neoplasms']  Lung Neoplasms  
141111  ['Lung Neoplasms']  Lung Neoplasms  
141353  ['Lung Neoplasms']  Lung Neoplasms  
141314  ['Lung Neoplasms']  Lung Neoplasms  

[495 rows x 8 columns]

In [97]:
verified_lung = ['hsa-mir-451a' 
,'hsa-mir-652'  
,'hsa-mir-557'  
,'hsa-mir-1228' 
,'hsa-mir-1207' 
,'hsa-mir-153'  
,'hsa-mir-206'  
,'hsa-mir-668'  
,'hsa-mir-487b' 
,'hsa-mir-184'  
,'hsa-mir-214'  
,'hsa-mir-205'  
,'hsa-mir-449a' 
,'hsa-mir-145' 
,'hsa-mir-1236'] 

results_Td_lung_neoplasm['y_true'][results_Td_lung_neoplasm['miRNA_y'].isin(verified_lung)] = 1
obtain_metrics(results_Td_lung_neoplasm)

tn = 458, fp = 9, fn = 4, tp = 24
y_pred: 0 = 462 | 1 = 33
y_true: 0 = 467 | 1 = 28
acc=0.9737|precision=0.7273|recall=0.8571|f1=0.7869|auc=0.9696|aupr=0.7666|pos_acc=0.8571|neg_acc=0.9913
0.9737, 0.7273, 0.8571, 0.7869, 0.9696, 0.7666, 0.8589, 0.8742, 0.7768


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-v

In [161]:
results_Td_lung_neoplasm.sort_values(by = 'y_prob', ascending = False, inplace = True)
obtain_metrics(results_Tm_let7a.iloc[:28])

tn = 0, fp = 1, fn = 0, tp = 27
y_pred: 0 = 0 | 1 = 28
y_true: 0 = 1 | 1 = 27
acc=0.9643|precision=0.9643|recall=1.0000|f1=0.9818|auc=0.7407|aupr=0.9893|pos_acc=1.0000|neg_acc=nan
0.9643, 0.9643, 1.0000, 0.9818, 0.7407, 0.9893, 0.9317, 0.9190, 0.9856


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:6: RuntimeWarning: invalid value encountered in true_divide
  


# hsa-let-7a

In [138]:
results_Tm_let7a = results_Tm.loc[results_Tm['miRNA_y'] == 'hsa-let-7a']
obtain_metrics(results_Tm_let7a)
results_Tm_let7a

tn = 326, fp = 12, fn = 12, tp = 33
y_pred: 0 = 338 | 1 = 45
y_true: 0 = 338 | 1 = 45
acc=0.9373|precision=0.7333|recall=0.7333|f1=0.7333|auc=0.9342|aupr=0.8095|pos_acc=0.7333|neg_acc=0.9645
0.9373, 0.7333, 0.7333, 0.7333, 0.9342, 0.8095, 0.8295, 0.8536, 0.7714


miRNA_x  disease_x  y_true  y_pred    y_prob     miRNA_y  \
76484         7        383     0.0     0.0  0.000028  hsa-let-7a   
27974         7        382     0.0     0.0  0.000453  hsa-let-7a   
108659        7        381     0.0     0.0  0.000020  hsa-let-7a   
167564        7        380     0.0     0.0  0.000089  hsa-let-7a   
156674        7        379     0.0     0.0  0.000004  hsa-let-7a   
...         ...        ...     ...     ...       ...         ...   
92819         7          5     0.0     0.0  0.000001  hsa-let-7a   
171029        7          4     0.0     0.0  0.000009  hsa-let-7a   
14114         7          3     1.0     0.0  0.000052  hsa-let-7a   
79949         7          2     0.0     0.0  0.000007  hsa-let-7a   
70049         7          1     0.0     0.0  0.000012  hsa-let-7a   

                                     disease_y  \
76484                  ['Wounds and Injuries']   
27974        ['Waldenstrom Macroglobulinemia']   
108659                            ['Vitiligo']   
167564                   ['Vascular Diseases']   
156674              ['Vascular Calcification']   
...                                        ...   
92819                    ['Acute Lung Injury']   
171029             ['Acute Coronary Syndrome']   
14114     ['ACTH-Secreting Pituitary Adenoma']   
79949   ['Acquired Immunodeficiency Syndrome']   
70049                   ['Abortion, Habitual']   

                                   disease  
76484                  Wounds and Injuries  
27974        Waldenstrom Macroglobulinemia  
108659                            Vitiligo  
167564                   Vascular Diseases  
156674              Vascular Calcification  
...                                    ...  
92819                    Acute Lung Injury  
171029             Acute Coronary Syndrome  
14114     ACTH-Secreting Pituitary Adenoma  
79949   Acquired Immunodeficiency Syndrome  
70049                   Abortion, Habitual  

[383 rows x 8 columns]

In [139]:
verified_let7a = ['Uterine Cervical Neoplasms'
,'Thyroid Neoplasms'
,'Sarcoma, Ewing'
,'Precursor Cell Lymphoblastic Leukemia-Lymphoma'
,'Carcinoma, Squamous Cell']

results_Tm_let7a['y_true'][results_Tm_let7a['disease'].isin(verified_let7a)] = 1
obtain_metrics(results_Tm_let7a)

tn = 326, fp = 7, fn = 12, tp = 38
y_pred: 0 = 338 | 1 = 45
y_true: 0 = 333 | 1 = 50
acc=0.9504|precision=0.8444|recall=0.7600|f1=0.8000|auc=0.9434|aupr=0.8431|pos_acc=0.7600|neg_acc=0.9645
0.9504, 0.8444, 0.7600, 0.8000, 0.9434, 0.8431, 0.8683, 0.8842, 0.8215


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#r

In [166]:
results_Tm_let7a.sort_values(by = 'y_prob', ascending = False, inplace = True)
obtain_metrics(results_Tm_let7a.iloc[:45])

tn = 0, fp = 7, fn = 0, tp = 38
y_pred: 0 = 0 | 1 = 45
y_true: 0 = 7 | 1 = 38
acc=0.8444|precision=0.8444|recall=1.0000|f1=0.9157|auc=0.7744|aupr=0.9555|pos_acc=1.0000|neg_acc=nan
0.8444, 0.8444, 1.0000, 0.9157, 0.7744, 0.9555, 0.8838, 0.8725, 0.9356


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:6: RuntimeWarning: invalid value encountered in true_divide
  


In [167]:
results_Tm_let7a.iloc[:50]

miRNA_x  disease_x  y_true  y_pred    y_prob     miRNA_y  \
166079        7        110     1.0     1.0  0.999996  hsa-let-7a   
38369         7        247     1.0     1.0  0.999994  hsa-let-7a   
41834         7         50     1.0     1.0  0.999993  hsa-let-7a   
147764        7        191     1.0     1.0  0.999992  hsa-let-7a   
117569        7        349     1.0     1.0  0.999992  hsa-let-7a   
168554        7        186     1.0     1.0  0.999990  hsa-let-7a   
2729          7         33     1.0     1.0  0.999989  hsa-let-7a   
6194          7        281     1.0     1.0  0.999976  hsa-let-7a   
101234        7        282     1.0     1.0  0.999975  hsa-let-7a   
61139         7        236     1.0     1.0  0.999956  hsa-let-7a   
161624        7        304     1.0     1.0  0.999936  hsa-let-7a   
103709        7        120     1.0     1.0  0.999891  hsa-let-7a   
174494        7        269     1.0     1.0  0.999861  hsa-let-7a   
14609         7        317     1.0     1.0  0.999854  hsa-let-7a   
54704         7         63     1.0     1.0  0.999844  hsa-let-7a   
106679        7        163     1.0     1.0  0.999821  hsa-let-7a   
56189         7        253     1.0     1.0  0.999814  hsa-let-7a   
10154         7         59     1.0     1.0  0.999814  hsa-let-7a   
160139        7        307     1.0     1.0  0.999504  hsa-let-7a   
153209        7        159     1.0     1.0  0.999470  hsa-let-7a   
143309        7        323     0.0     1.0  0.998583  hsa-let-7a   
24014         7        341     1.0     1.0  0.998041  hsa-let-7a   
51734         7        219     1.0     1.0  0.997572  hsa-let-7a   
74009         7        347     1.0     1.0  0.996381  hsa-let-7a   
187859        7        119     1.0     1.0  0.995681  hsa-let-7a   
37379         7         11     1.0     1.0  0.991649  hsa-let-7a   
143804        7        328     1.0     1.0  0.986620  hsa-let-7a   
149744        7         92     1.0     1.0  0.982001  hsa-let-7a   
6689          7        226     0.0     1.0  0.977932  hsa-let-7a   
135389        7        232     0.0     1.0  0.975626  hsa-let-7a   
45299         7         65     1.0     1.0  0.971946  hsa-let-7a   
127469        7        257     0.0     1.0  0.970088  hsa-let-7a   
19064         7         93     1.0     1.0  0.954116  hsa-let-7a   
185879        7        126     1.0     1.0  0.951107  hsa-let-7a   
122024        7        145     1.0     1.0  0.908750  hsa-let-7a   
32924         7         61     1.0     1.0  0.870438  hsa-let-7a   
64109         7        268     1.0     1.0  0.865810  hsa-let-7a   
119549        7        252     0.0     1.0  0.830392  hsa-let-7a   
121034        7        147     0.0     1.0  0.796463  hsa-let-7a   
33914         7        321     1.0     1.0  0.794034  hsa-let-7a   
164099        7        239     1.0     1.0  0.710789  hsa-let-7a   
92324         7        378     1.0     1.0  0.698286  hsa-let-7a   
167069        7        364     1.0     1.0  0.566669  hsa-let-7a   
149249        7        370     1.0     1.0  0.540227  hsa-let-7a   
112619        7        185     0.0     1.0  0.503388  hsa-let-7a   
118064        7         72     0.0     0.0  0.481215  hsa-let-7a   
104204        7        377     0.0     0.0  0.436514  hsa-let-7a   
99254         7         97     0.0     0.0  0.388731  hsa-let-7a   
148754        7        142     1.0     0.0  0.328215  hsa-let-7a   
60644         7         44     0.0     0.0  0.299106  hsa-let-7a   

                                                disease_y  \
166079                     ['Digestive System Neoplasms']   
38369                      ['Lymphoma, Primary Effusion']   
41834                                ['Breast Neoplasms']   
147764                                   ['Inflammation']   
117569                                ['Sarcoma, Kaposi']   
168554                                    ['Hypertrophy']   
2729                                           ['Asthma']   
6194                         ['Nasopharyngeal Neopl

# hsa-let-7b

In [151]:
results_Tm_let7b = results_Tm.loc[results_Tm['miRNA_y'] == 'hsa-let-7b']
results_Tm_let7b['y_pred'][results_Tm_let7b['disease'].str.contains('Sarcoma, Ewing')] = 1
obtain_metrics(results_Tm_let7b)
results_Tm_let7b

tn = 320, fp = 25, fn = 8, tp = 30
y_pred: 0 = 328 | 1 = 55
y_true: 0 = 345 | 1 = 38
acc=0.9138|precision=0.5455|recall=0.7895|f1=0.6452|auc=0.9361|aupr=0.8306|pos_acc=0.7895|neg_acc=0.9756
0.9138, 0.5455, 0.7895, 0.6452, 0.9361, 0.8306, 0.8031, 0.8314, 0.7379


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a

miRNA_x  disease_x  y_true  y_pred    y_prob     miRNA_y  \
76307       117        383     0.0     0.0  0.000812  hsa-let-7b   
27797       117        382     0.0     0.0  0.000913  hsa-let-7b   
108482      117        381     0.0     0.0  0.000015  hsa-let-7b   
167387      117        380     0.0     0.0  0.000746  hsa-let-7b   
156497      117        379     0.0     0.0  0.000083  hsa-let-7b   
...         ...        ...     ...     ...       ...         ...   
92642       117          5     0.0     0.0  0.000002  hsa-let-7b   
170852      117          4     0.0     0.0  0.000169  hsa-let-7b   
13937       117          3     0.0     1.0  0.994640  hsa-let-7b   
79772       117          2     0.0     0.0  0.000030  hsa-let-7b   
69872       117          1     0.0     0.0  0.000021  hsa-let-7b   

                                     disease_y  \
76307                  ['Wounds and Injuries']   
27797        ['Waldenstrom Macroglobulinemia']   
108482                            ['Vitiligo']   
167387                   ['Vascular Diseases']   
156497              ['Vascular Calcification']   
...                                        ...   
92642                    ['Acute Lung Injury']   
170852             ['Acute Coronary Syndrome']   
13937     ['ACTH-Secreting Pituitary Adenoma']   
79772   ['Acquired Immunodeficiency Syndrome']   
69872                   ['Abortion, Habitual']   

                                   disease  
76307                  Wounds and Injuries  
27797        Waldenstrom Macroglobulinemia  
108482                            Vitiligo  
167387                   Vascular Diseases  
156497              Vascular Calcification  
...                                    ...  
92642                    Acute Lung Injury  
170852             Acute Coronary Syndrome  
13937     ACTH-Secreting Pituitary Adenoma  
79772   Acquired Immunodeficiency Syndrome  
69872                   Abortion, Habitual  

[383 rows x 8 columns]

In [153]:
verified_let7b = ['Thyroid Neoplasms'
#,'\["Sarcoma, Ewing\'s"\]'
,'Periodontitis'
,'Mesothelioma'
,'Glioblastoma'
,'Gastrointestinal Neoplasms'
# ,'Carcinoma'
,'Carcinoma, Small Cell'
,'Adenocarcinoma'
,'Pituitary Adenoma']

results_Tm_let7b['y_true'][results_Tm_let7b['disease'].str.contains('Sarcoma, Ewing')] = 1

results_Tm_let7b['y_true'][results_Tm_let7b['disease'].isin(verified_let7b)] = 1
obtain_metrics(results_Tm_let7b)

tn = 320, fp = 16, fn = 8, tp = 39
y_pred: 0 = 328 | 1 = 55
y_true: 0 = 336 | 1 = 47
acc=0.9373|precision=0.7091|recall=0.8298|f1=0.7647|auc=0.9488|aupr=0.8574|pos_acc=0.8298|neg_acc=0.9756
0.9373, 0.7091, 0.8298, 0.7647, 0.9488, 0.8574, 0.8565, 0.8771, 0.8111


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if sys.path[0] == '':
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/ind

In [160]:
results_Tm_let7b.sort_values(by = 'y_prob', ascending = False, inplace = True)
obtain_metrics(results_Tm_let7b.iloc[:47])

tn = 0, fp = 11, fn = 0, tp = 36
y_pred: 0 = 0 | 1 = 47
y_true: 0 = 11 | 1 = 36
acc=0.7660|precision=0.7660|recall=1.0000|f1=0.8675|auc=0.8965|aupr=0.9693|pos_acc=1.0000|neg_acc=nan
0.7660, 0.7660, 1.0000, 0.8675, 0.8965, 0.9693, 0.8795, 0.8748, 0.9184


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:6: RuntimeWarning: invalid value encountered in true_divide
  


# hsa-mir-1

In [92]:
results_Tm_mir1 = results_Tm.loc[results_Tm['miRNA_y'] == 'hsa-mir-1']
obtain_metrics(results_Tm_mir1)
results_Tm_mir1

tn = 312, fp = 25, fn = 14, tp = 32
y_pred: 0 = 326 | 1 = 57
y_true: 0 = 337 | 1 = 46
acc=0.8982|precision=0.5614|recall=0.6957|f1=0.6214|auc=0.9422|aupr=0.6882|pos_acc=0.6957|neg_acc=0.9571
0.8982, 0.5614, 0.6957, 0.6214, 0.9422, 0.6882, 0.7571, 0.7875, 0.6548


miRNA_x  disease_x  y_true  y_pred    y_prob    miRNA_y  \
76267        15        383     0.0     0.0  0.015560  hsa-mir-1   
27757        15        382     0.0     0.0  0.000578  hsa-mir-1   
108442       15        381     0.0     0.0  0.389731  hsa-mir-1   
167347       15        380     0.0     0.0  0.010214  hsa-mir-1   
156457       15        379     0.0     0.0  0.000080  hsa-mir-1   
...         ...        ...     ...     ...       ...        ...   
92602        15          5     0.0     0.0  0.000031  hsa-mir-1   
170812       15          4     1.0     1.0  0.996028  hsa-mir-1   
13897        15          3     0.0     0.0  0.272389  hsa-mir-1   
79732        15          2     0.0     0.0  0.000160  hsa-mir-1   
69832        15          1     0.0     0.0  0.033981  hsa-mir-1   

                                     disease_y  \
76267                  ['Wounds and Injuries']   
27757        ['Waldenstrom Macroglobulinemia']   
108442                            ['Vitiligo']   
167347                   ['Vascular Diseases']   
156457              ['Vascular Calcification']   
...                                        ...   
92602                    ['Acute Lung Injury']   
170812             ['Acute Coronary Syndrome']   
13897     ['ACTH-Secreting Pituitary Adenoma']   
79732   ['Acquired Immunodeficiency Syndrome']   
69832                   ['Abortion, Habitual']   

                                   disease  
76267                  Wounds and Injuries  
27757        Waldenstrom Macroglobulinemia  
108442                            Vitiligo  
167347                   Vascular Diseases  
156457              Vascular Calcification  
...                                    ...  
92602                    Acute Lung Injury  
170812             Acute Coronary Syndrome  
13897     ACTH-Secreting Pituitary Adenoma  
79732   Acquired Immunodeficiency Syndrome  
69832                   Abortion, Habitual  

[383 rows x 8 columns]

In [168]:
verified_mir1 = ['Reperfusion Injury'
,'Pancreatic Neoplasms'
,'Neuroblastoma'
,'Neoplasms'
,'Myocytes, Cardiac'
,'Muscular Disorders, Atrophic'
,'Mesothelioma'
,'Leukemia, Myeloid, Acute'
,'Glioblastoma'
,'Esophageal Neoplasms'
,'Cardiomyopathy, Dilated'
,'Carcinoma, Renal Cell'
,'Carcinoma'
,'Atrial Fibrillation'
,'Adenocarcinoma']

results_Tm_mir1['y_true'][results_Tm_mir1['disease'].isin(verified_mir1)] = 1
obtain_metrics(results_Tm_mir1)

tn = 312, fp = 10, fn = 14, tp = 47
y_pred: 0 = 326 | 1 = 57
y_true: 0 = 322 | 1 = 61
acc=0.9373|precision=0.8246|recall=0.7705|f1=0.7966|auc=0.9684|aupr=0.8646|pos_acc=0.7705|neg_acc=0.9571
0.9373, 0.8246, 0.7705, 0.7966, 0.9684, 0.8646, 0.8731, 0.8917, 0.8306


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/pandas/core/generic.py:9114: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-v

In [176]:
results_Tm_mir1.sort_values(by = 'y_prob', ascending = False, inplace = True)
obtain_metrics(results_Tm_mir1.iloc[:57])

tn = 0, fp = 10, fn = 0, tp = 47
y_pred: 0 = 0 | 1 = 57
y_true: 0 = 10 | 1 = 47
acc=0.8246|precision=0.8246|recall=1.0000|f1=0.9038|auc=0.7191|aupr=0.9202|pos_acc=1.0000|neg_acc=nan
0.8246, 0.8246, 1.0000, 0.9038, 0.7191, 0.9202, 0.8577, 0.8419, 0.9120


/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/home/chujunyi/anaconda3/envs/python36/lib/python3.6/site-packages/ipykernel_launcher.py:6: RuntimeWarning: invalid value encountered in true_divide
  


# hsa-mir-25

In [90]:
results_Tm_mir25 = results_Tm.loc[results_Tm['miRNA_y'] == 'hsa-mir-25']
obtain_metrics(results_Tm_mir25)
results_Tm_mir25

tn = 353, fp = 7, fn = 13, tp = 10
y_pred: 0 = 366 | 1 = 17
y_true: 0 = 360 | 1 = 23
acc=0.9478|precision=0.5882|recall=0.4348|f1=0.5000|auc=0.9028|aupr=0.6009|pos_acc=0.4348|neg_acc=0.9645
0.9478, 0.5882, 0.4348, 0.5000, 0.9028, 0.6009, 0.6949, 0.7379, 0.5505


miRNA_x  disease_x  y_true  y_pred    y_prob     miRNA_y  \
76515        48        383     0.0     0.0  0.000006  hsa-mir-25   
28005        48        382     0.0     0.0  0.000017  hsa-mir-25   
108690       48        381     0.0     0.0  0.000015  hsa-mir-25   
167595       48        380     0.0     0.0  0.000035  hsa-mir-25   
156705       48        379     0.0     0.0  0.000014  hsa-mir-25   
...         ...        ...     ...     ...       ...         ...   
92850        48          5     0.0     0.0  0.000004  hsa-mir-25   
171060       48          4     0.0     0.0  0.000013  hsa-mir-25   
14145        48          3     0.0     0.0  0.000028  hsa-mir-25   
79980        48          2     0.0     0.0  0.000018  hsa-mir-25   
70080        48          1     0.0     0.0  0.000004  hsa-mir-25   

                                     disease_y  \
76515                  ['Wounds and Injuries']   
28005        ['Waldenstrom Macroglobulinemia']   
108690                            ['Vitiligo']   
167595                   ['Vascular Diseases']   
156705              ['Vascular Calcification']   
...                                        ...   
92850                    ['Acute Lung Injury']   
171060             ['Acute Coronary Syndrome']   
14145     ['ACTH-Secreting Pituitary Adenoma']   
79980   ['Acquired Immunodeficiency Syndrome']   
70080                   ['Abortion, Habitual']   

                                   disease  
76515                  Wounds and Injuries  
28005        Waldenstrom Macroglobulinemia  
108690                            Vitiligo  
167595                   Vascular Diseases  
156705              Vascular Calcification  
...                                    ...  
92850                    Acute Lung Injury  
171060             Acute Coronary Syndrome  
14145     ACTH-Secreting Pituitary Adenoma  
79980   Acquired Immunodeficiency Syndrome  
70080                   Abortion, Habitual  

[383 rows x 8 columns]

# hsa-mir-499

In [91]:
results_Tm_mir499 = results_Tm.loc[results_Tm['miRNA_y'].str.contains('hsa-mir-499')]
obtain_metrics(results_Tm_mir499)
results_Tm_mir499

tn = 717, fp = 28, fn = 8, tp = 13
y_pred: 0 = 725 | 1 = 41
y_true: 0 = 745 | 1 = 21
acc=0.9530|precision=0.3171|recall=0.6190|f1=0.4194|auc=0.9319|aupr=0.5907|pos_acc=0.6190|neg_acc=0.9890
0.9530, 0.3171, 0.6190, 0.4194, 0.9319, 0.5907, 0.6824, 0.7238, 0.5050


miRNA_x  disease_x  y_true  y_pred        y_prob       miRNA_y  \
76683         3        383     0.0     0.0  2.063776e-04  hsa-mir-499a   
76397       322        383     0.0     0.0  3.146673e-06  hsa-mir-499b   
28173         3        382     0.0     0.0  9.189659e-04  hsa-mir-499a   
27887       322        382     0.0     0.0  8.980661e-07  hsa-mir-499b   
108572      322        381     0.0     0.0  6.946107e-06  hsa-mir-499b   
...         ...        ...     ...     ...           ...           ...   
14027       322          3     0.0     0.0  9.409354e-07  hsa-mir-499b   
80148         3          2     0.0     0.0  4.271657e-06  hsa-mir-499a   
79862       322          2     0.0     0.0  1.278925e-06  hsa-mir-499b   
70248         3          1     1.0     0.0  3.690497e-05  hsa-mir-499a   
69962       322          1     0.0     0.0  7.071166e-06  hsa-mir-499b   

                                     disease_y  \
76683                  ['Wounds and Injuries']   
76397                  ['Wounds and Injuries']   
28173        ['Waldenstrom Macroglobulinemia']   
27887        ['Waldenstrom Macroglobulinemia']   
108572                            ['Vitiligo']   
...                                        ...   
14027     ['ACTH-Secreting Pituitary Adenoma']   
80148   ['Acquired Immunodeficiency Syndrome']   
79862   ['Acquired Immunodeficiency Syndrome']   
70248                   ['Abortion, Habitual']   
69962                   ['Abortion, Habitual']   

                                   disease  
76683                  Wounds and Injuries  
76397                  Wounds and Injuries  
28173        Waldenstrom Macroglobulinemia  
27887        Waldenstrom Macroglobulinemia  
108572                            Vitiligo  
...                                    ...  
14027     ACTH-Secreting Pituitary Adenoma  
80148   Acquired Immunodeficiency Syndrome  
79862   Acquired Immunodeficiency Syndrome  
70248                   Abortion, Habitual  
69962                   Abortion, Habitual  

[766 rows x 8 columns]